# Selection tool

In [ ]:
import datetime as dt
from pathlib import Path
import pandas as pd

import hvplot.pandas
import panel as pn
import param

pn.extension()

In [ ]:
print(f'panel: {pn.__version__}\nparam: {param.__version__}\nhvplot: {hvplot.__version__}')

In [ ]:
class Component(param.Parameterized):
    """Class with interactive parameters for indicating component preferences."""
    scalability       = param.Integer(3,bounds=(0,5),doc='Scale to more data')
    deployability     = param.Integer(3,bounds=(0,5),doc='Deployability')
    integratability   = param.Integer(3,bounds=(0,5),doc='Tool support / integration')

    
#     @param.depends('interactivity','code','deployability','setup','documentation','community','integration','licence')
    def view_bar(self):
        df = self.return_dataf()
        return (df
                .hvplot.bar(xlabel='criteria',ylabel='score')
                .opts(xrotation=45,title=self.name,ylim=(0,5),show_grid=True,width=400))
    
    def view(self):
        expand_layout = pn.Column()
        return pn.Row(self.param,self.view_bar,self.return_dataf)
        

    def return_dataf(self):
        return (pd.DataFrame([x for x in self.param.get_param_values() if not x[0]=='name'],
                            columns=(['criterion',self.name]))
                .set_index('criterion'))
    

In [ ]:
class Weights(Component):
    """Class with weights for all the criteria defined in Component."""
    pass
    

In [ ]:
class Viewer(param.Parameterized):
    """Class that combines all settable objects (component & weights) into an overview GUI."""
    
    # create all component objects.
    names = ['foo','bar']
    components = [Component(name=name) for name in names]
    component = param.ObjectSelector(default=components[0], objects=components)
    
    # create weights.
    weights = Weights()
    
    # boolean switch bar display button
    set_criteria_as_outer_and_tools_as_inner_label = param.Boolean(default=True)
    
    # methods
    def get_dataf(self):
        objects = self.param['component'].objects
        df_list = [comp.return_dataf() for comp in objects]
        df = pd.DataFrame.join(df_list[0],df_list[1:])
        return df
    
    @param.depends('component')
    def view(self):
        return pn.panel(self.param)
        
    def pane_separate_bar(self):
        return pn.Row(pn.Param(self.param, parameters=['component'], show_name=False, expand=True), self.component.view_bar)
    
    @param.depends('component.param',
                   'set_criteria_as_outer_and_tools_as_inner_label',watch=True)
    def pane_combined_bar(self):
        df = self.get_dataf()
        if self.set_criteria_as_outer_and_tools_as_inner_label:
            index = ['criterion','tool']
        else:
            index = ['tool','criterion']
        return pn.Column(self.param['set_criteria_as_outer_and_tools_as_inner_label'],
                         df.reset_index()
                         .melt(id_vars='criterion',var_name='tool',value_name='score')
                         .set_index(index)
                         .hvplot.bar().opts(xrotation=90,width=1000)
                        )

    @param.depends('component.param',
                   'weights.param',watch=True)
    def compute_weighted(self):
        df_all = self.get_dataf()
        f_scale = self.weights.return_dataf().sum(axis=0)[0]
        return pn.Row(self.weights.param,
                      pd.DataFrame(data=(df_all.values*self.weights.return_dataf().values).sum(axis=0),
                                   index=df_all.columns,
                                   columns=['weighted_score'])
                      .transpose()
                      .hvplot.bar().opts(show_grid=True))
    
    @param.depends('component.param',
                   'weights.param',
                   'set_criteria_as_outer_and_tools_as_inner_label',watch=True,)
    def panel_tabs(self):
        return pn.Tabs(('single',self.pane_separate_bar),
                       ('combined',self.pane_combined_bar),
                       ('weighted',self.compute_weighted))
    
    
    def panel_full(self):
        description = '## Selection tool\nThis tool assist users to indicate their preferences for different components. For each component, scores between 0-5 can be given. In the weights tab each criterion can be weighted which allows aggregating all criteria to one single cost function'
        return pn.Column(description,self.panel_tabs)
    

In [ ]:
viewer = Viewer()

param.scalability = 5
viewer.weights.deployability = 2
viewer.weights.integratability = 5

viewer.component.scalability = 4
viewer.component.deployability = 1
viewer.component.integratability = 5

In [ ]:
viewer.panel_full().servable()

In [ ]:
viewer.panel_tabs().servable()